## Imports

In [337]:
from premise import *
import bw2data as bd
import bw2io as bo
import numpy as np
import pandas as pd
#import brightway2 as bw

### Project set up

In [338]:
bd.projects.set_current("MPTEX")

In [339]:
bo.bw2setup()

Biosphere database already present!!! No setup is needed


In [340]:
bd.databases

Databases dictionary with 4 object(s):
	SSP2-RCP19-2050
	biosphere3
	ecoinvent 3.9.1 cutoff
	image-SSP2-RCP19-2020

In [341]:
# file path to the place with the ecoinvent spold files (datasets directory)
fpei39 = "/etc/data/ecospold/datasets"
if 'ecoinvent 3.9.1 cutoff' in bd.databases:
    print("Database has already been imported")
else:
    ei39 = bo.SingleOutputEcospold2Importer(fpei39, 'ecoinvent 3.9.1 cutoff')
    ei39.apply_strategies()
    ei39.statistics()
    
    if len(list(ei39.unlinked)) == 0:
        ei39.write_database()

Database has already been imported


In [124]:
ndb = NewDatabase(
    scenarios=[
        {"model":"image", "pathway":"SSP2-RCP19", "year":2020},
        #{"model":"image", "pathway":"SSP2-RCP19", "year":2030},
        #{"model":"image", "pathway":"SSP2-RCP19", "year":2050},
        #{"model":"remind","pathway":"SSP2-Base","year":2039}
    ],
    source_db="ecoinvent 3.9.1 cutoff", # <-- name of the database in the BW2 project. Must be a string.
    source_version="3.9", # <-- version of ecoinvent. Can be "3.5", "3.6", "3.7" or "3.8". Must be a string.
    key='tUePmX_S5B8ieZkkM7WUU2CnO8SmShwmAeWK9x2rTFo=' # <-- decryption key
    # to be requested from the library maintainers if you want ot use default scenarios included in `premise`
)

premise v.(2, 1, 0)
+------------------------------------------------------------------+
| Warning                                                          |
+------------------------------------------------------------------+
| Because some of the scenarios can yield LCI databases            |
| containing net negative emission technologies (NET),             |
| it is advised to account for biogenic CO2 flows when calculating |
| Global Warming potential indicators.                             |
| `premise_gwp` provides characterization factors for such flows.  |
| It also provides factors for hydrogen emissions to air.          |
|                                                                  |
| Within your bw2 project:                                         |
| from premise_gwp import add_premise_gwp                          |
| add_premise_gwp()                                                |
+------------------------------------------------------------------+
+-------------

In [125]:
ndb.update()

Processing scenarios: 100%|█████████████| 1/1 [01:23<00:00, 83.01s/it]

Done!



In [126]:
#Save as a database
ndb.write_db_to_brightway(name=["image-SSP2-RCP19-2020",])

Write new database(s) to Brightway.
Running all checks...
Minor anomalies found: check the change report.
Title: Writing activities to SQLite3 database:
  Started: 05/23/2024 15:57:34
  Finished: 05/23/2024 15:58:06
  Total time elapsed: 00:00:32
  CPU %: 100.00
  Memory %: 3.27
Created database: image-SSP2-RCP19-2020
Generate scenario report.
Report saved under /home/jupyter-xtdds_s2024/MPTEX/export/scenario_report.
Generate change report.
Report saved under /home/jupyter-xtdds_s2024/MPTEX.


In [21]:
# Trouble shooting : 
#ds = bd.get_activity(('biosphere3', 'd3260d0e-8203-4cbb-a45a-6a13131a5108'))
#print(ds['name'])

NMVOC, non-methane volatile organic compounds


## PV dataset look-up

In [23]:
# import wurst
# database = wurst.extract_brightway2_databases("SSP2-RCP19-2050")

Getting activity data


100%|██████████| 40657/40657 [00:00<00:00, 289588.27it/s]


Adding exchange data to activities


100%|██████████| 1524505/1524505 [00:28<00:00, 52748.02it/s] 


Filling out exchange data


100%|██████████| 40657/40657 [00:01<00:00, 21473.10it/s]


In [24]:
# import pickle
# with open(r"ei391.pickle", "wb") as output_file:
#     pickle.dump(database, output_file)

In [25]:
# def load_db():
#     with open(r"ei391.pickle", "rb") as input_file:
#         db = pickle.load(input_file)

#     for ds in db:
#         if "categories" in ds:
#             del ds["categories"]
            
#     return db

In [26]:
# db = load_db()

In [57]:
# import wurst.searching as ws

# e_mixes = ws.get_many(db,
#         ws.contains("name","market for electricity")
#                      )


# #solar_pv = ws.get_many(db, 
# #    ws.contains("name", "photovoltaic")
# #)

# #print(e_mixes)
# counter = 0
# for ds in e_mixes:
#     counter+=1
#     #print(ds.keys())
#     for exc in ds['exchanges']:
#         if 'photovoltaic' in exc['name'] :
#             print(ds['name'],ds['location'],'--->',exc['name'])
#         #else :
#         #    print(ds['name'],exc['name'])

# print(counter)
#for ds in e_mixes :
#    print(ds['name'],ds['location'])





market for electricity, low voltage, renewable energy products CH ---> electricity production, photovoltaic, 3kWp slanted-roof installation, single-Si, panel, mounted, renewable energy produc
market for electricity, low voltage, renewable energy products CH ---> electricity production, photovoltaic, 3kWp slanted-roof installation, multi-Si, panel, mounted, renewable energy product
615


In [ ]:
for ds in solar_pv:
    print(ds["name"],ds['location'])

In [342]:
def pv_market_mixes_identifier(db_name) :
    """
    Function to list and parse pv datasets affecting an energy grid mix.
    """
    market_group_ds_storage = []
    market_ds_storage = []
    storage = []

    market_group_ds = []
    market_ds = []

    # Strategy filtering : is the dataset part of a market group or a basic market electricity grid mix 
    for ds in bd.Database(db_name) : 
        if 'market for electricity' in ds['name'] :
            group_counter = 0
            for exc in ds.exchanges(): 
                if 'market group for electricity' in exc['name'] : 
                    group_counter +=1 
            if group_counter == 0 : 
                market_ds.append((ds['name'],ds['code'])) 
            else : 
                market_group_ds.append((ds['name'],ds['location'],exc['input']))

    # Find if there are pv technologies involved with any of the market datasets : 
    for market in market_ds : 
        ds = bd.get_activity((db_name,market[1]))
        for exc in ds.exchanges() :
            if 'photovoltaic' in exc.input['name'] :
                # Extract the dataset name
                dataset_name = exc.input['name'] 
                # Make the name usable
                parsed_name = pv_name_parser(dataset_name)
                if 'roof' in parsed_name[1] : 
                    parsed_name.append(' on roof')
                elif 'facade' in parsed_name[1] : 
                    parsed_name.append('at building')
                else :
                    parsed_name.append('on open ground')
                
                # skip non pv energy producing datasets 
                if not any('kWp' in s for s in parsed_name) : 
                    continue  
                # Clear the kWp unit from the name
                parsed_name = [sub.replace('kWp','') for sub in parsed_name]
                # Store the market datasets and relevant information :
                market_ds_storage.append((ds['name'],ds['location'],np.nan,exc.input['code'],*parsed_name))
                
    # Find if there are pv technologies involved with any of the market GROUP datasets : 
    for market_group in market_group_ds : 
        group_ds = bd.get_activity((market_group[2]))
        # Note : the market groups typically have an intermediate dataset splitting commercial/residential
        for exc in group_ds.exchanges(): 
            if 'photovoltaic' in exc.input['name']: 
                production_sector = bd.get_activity((db_name,exc.input['code']))

                # Find the specific pv dataset technology & unit quantity
                for exc2 in production_sector.exchanges():
                    if 'photovoltaic' in exc2['name'] :
                        #print(exc2['name'],exc2['location'],exc2['unit'], exc['type'],exc2['amount'])
                        
                        # Extract the dataset name
                        parsed_name = pv_name_parser(exc2['name'])
                        # skip non pv energy producing datasets 
                        if not any('kWp' in s for s in parsed_name) : 
                            continue
                        # Clear the kWp unit from the name (it is already implied in the column name
                        parsed_name = [sub.replace('kWp','') for sub in parsed_name]                            
                        market_group_ds_storage.append((market_group[0],market_group[1],group_ds['location'],(production_sector['code'],exc2.input['code']),*parsed_name))

    # Convert to pd dataframe 
    cols_group = ['Market Dataset','ecoinvent location','Market group location','Underlying PV tech code','Installation','Peak power (kWp)','Technology','Placement','Build','Placement2']
    cols_ds = ['Market Dataset','ecoinvent location','Market group location','Underlying PV tech code','Peak power (kWp)','Installation','Technology','Placement','Build','Placement2']
    
    df1 = pd.DataFrame(market_ds_storage,columns = cols_ds)
    df2 = pd.DataFrame(market_group_ds_storage,columns = cols_group) 
    df3 = pd.concat([df1,df2])
    df3['Peak power (kWp)'] = df3['Peak power (kWp)'].astype(int)
    return df3


def pv_name_parser(ds_name): 
    """
    Extract technical information from the dataset names
    Clean up the string if there are empty fields
    """
    strings = ds_name.replace('electricity production,','')
    strings = strings.replace('photovoltaic','')
    strings = strings.replace('installation','')
    strings = strings.replace('kWp','kWp,')
    strings = str(strings).split(',')
    # Some of the elements might have returned empty or a space, lets clear that
    strings = list(filter(None, strings))
    strings = [i for i in strings if i !=" "]
    strings = [i for i in strings if "renewable" not in i]
    return strings

the_db = 'ecoinvent 3.9.1 cutoff'
the_other_db = 'SSP2-RCP19-2050'
the_other_db2 = 'image-SSP2-RCP19-2020'
pv_datasets = pv_market_mixes_identifier(the_other_db2)    
display(pv_datasets)

Market Dataset ecoinvent location  \
0      market for electricity, low voltage, renewable...                 CH   
1      market for electricity, low voltage, renewable...                 CH   
0                   market for electricity, high voltage                 ET   
1                   market for electricity, high voltage                 ET   
2                   market for electricity, high voltage                 ET   
...                                                  ...                ...   
14116                market for electricity, low voltage              CA-BC   
14117                market for electricity, low voltage              CA-BC   
14118                market for electricity, low voltage              CA-BC   
14119                market for electricity, low voltage              CA-BC   
14120                market for electricity, low voltage              CA-BC   

      Market group location  \
0                       NaN   
1                       NaN   
0                       EAF   
1                       EAF   
2                       EAF   
...                     ...   
14116                   CAN   
14117                   CAN   
14118                   CAN   
14119                   CAN   
14120                   CAN   

                                 Underlying PV tech code  Peak power (kWp)  \
0                       b0b8dacb783da5158538cac3bbf1ce88                 3   
1                       b5dae48681351a2f70efde3e7d2be6dd                 3   
0      (b1aeaf37d0bd4027abc939b89d39e693, 90e8cd12bbf...               156   
1      (b1aeaf37d0bd4027abc939b89d39e693, 9a6bb4142ca...               156   
2      (b1aeaf37d0bd4027abc939b89d39e693, d62e007d22e...               570   
...                                                  ...               ...   
14116  (10b4122ac22b41aba6a007c810296a90, c8234c88a5e...                 3   
14117  (10b4122ac22b41aba6a007c810296a90, be605eaacd9...                 3   
14118  (10b4122ac22b41aba6a007c810296a90, 0f97cf00e49...                 3   
14119  (10b4122ac22b41aba6a007c810296a90, bc96527e31b...                 3   
14120  (10b4122ac22b41aba6a007c810296a90, f63648bbd67...                 3   

         Installation  Technology        Placement        Build Placement2  
0       slanted-roof    single-Si            panel      mounted    on roof  
1       slanted-roof     multi-Si            panel      mounted    on roof  
0          flat-roof     multi-Si          on roof         None       None  
1          flat-roof    single-Si          on roof         None       None  
2        open ground          CIS   on open ground         None       None  
...               ...         ...              ...          ...        ...  
14116   slanted-roof         CdTe        laminated   integrated    on roof  
14117   slanted-roof     multi-Si        laminated   integrated    on roof  
14118   slanted-roof     multi-Si            panel      mounted    on roof  
14119   slanted-roof    single-Si        laminated   integrated    on roof  
14120   slanted-roof    single-Si            panel      mounted    on roof  

[14123 rows x 10 columns]

In [358]:
pv_datasets['fake_efficiencies'] = 1400
#display(pv_datasets)

# def retrieve_new_pv_production(pv_datasets):
#    """See with Edgar and Terry"""
#    pd.DataFrame(expected_market_pv_productions)
#    return expected_market_pv_productions

def update_pv_efficiencies(pv_datasets) : 

    """
    ADD description here
    Find a way to indicate WHICH database is assessed (remove references to "the_other_db2")
    """
    pv_db = pv_datasets.copy()

    lifetime_kwh = []
    new_lifetime_kwh = []
    Ratio = []

    # Mapping tables for premise databases 
    market_group_mapping_com = pd.read_excel('pv_com_res_shares.xlsx',sheet_name = 1,index_col = 0)
    market_group_mapping_res = pd.read_excel('pv_com_res_shares.xlsx',sheet_name = 0,index_col = 0)
    #display(market_group_mapping_com)
    
    for row in pv_db.iterrows() : 
        code = row[1]['Underlying PV tech code']
        new_prod = row[1]['fake_efficiencies']*row[1]['Peak power (kWp)']*30
        new_lifetime_kwh.append(new_prod)
        #location = row[1]['ecoinvent location'] 
        
        if type(code) == tuple :
            #continue
            ds = bd.get_activity((the_other_db2,code[0]))
            location = ds['location']
            # Select residential or commercial : 
            tech_ds = bd.get_activity((the_other_db2, code[1]))
            
            common_naming = [str(i) for i in row[1][4:-1] if i != None] 
            common_name = common_naming[0]+' kWp'+common_naming[1]+ 'installation,'
            common_name = common_name+','.join(common_naming[2:])
        
            #print(ds['name'],ds['location'],'-->',common_name)
            
            if 'commercial' in ds['name'] : 
                #map_value.append(market_group_mapping_com.loc[location,common_name])
                map_val = market_group_mapping_com.loc[location,common_name]
            
            if 'residential' in ds['name']:
                #map_value.append(market_group_mapping_res.loc[location,common_name])
                map_val = market_group_mapping_res.loc[location,common_name]
        
            # Script to find the exchange amount
            for exc in ds.exchanges():                
                if exc.input['code'] == tech_ds['code'] :
                    old_prod = map_val/exc['amount']
                    lifetime_kwh.append(old_prod)      

                    #exc['amount'] *= old_prod/new_prod 
                    #exc.save()
                    Ratio.append(old_prod/new_prod)
                  
        else :
            code = row[1]['Underlying PV tech code']
            ds = bd.get_activity((the_other_db2,code))

            #print(ds['name'])
            for exc in ds.exchanges():
                if exc['type'] == 'production' : 
                    output = exc['amount'] 
                    
                    #print(exc['amount'],exc['type'],exc['unit'])
                if ('photovoltaic' in exc['name']) & (exc['unit']=='unit') & ('kWp' in exc['name']) :
            #        print(exc['amount'],exc['unit'],exc['name'])
                    exc_amnt = exc['amount']
            old_prod = output/exc_amnt
            
            #print('Regular market!')
            # Placeholders
            lifetime_kwh.append(old_prod)
            Ratio.append(old_prod/new_prod)

            #exc['amount'] *= old_prod/new_prod 
            #exc.save()
    
    pv_db['previous production'] = lifetime_kwh  
    pv_db['new production'] = new_lifetime_kwh
    pv_db['Exchange Variation'] = Ratio
    return pv_db

pv_datasets1 = update_pv_efficiencies(pv_datasets)
display(pv_datasets1)

Market Dataset ecoinvent location  \
0      market for electricity, low voltage, renewable...                 CH   
1      market for electricity, low voltage, renewable...                 CH   
0                   market for electricity, high voltage                 ET   
1                   market for electricity, high voltage                 ET   
2                   market for electricity, high voltage                 ET   
...                                                  ...                ...   
14116                market for electricity, low voltage              CA-BC   
14117                market for electricity, low voltage              CA-BC   
14118                market for electricity, low voltage              CA-BC   
14119                market for electricity, low voltage              CA-BC   
14120                market for electricity, low voltage              CA-BC   

      Market group location  \
0                       NaN   
1                       NaN   
0                       EAF   
1                       EAF   
2                       EAF   
...                     ...   
14116                   CAN   
14117                   CAN   
14118                   CAN   
14119                   CAN   
14120                   CAN   

                                 Underlying PV tech code  Peak power (kWp)  \
0                       b0b8dacb783da5158538cac3bbf1ce88                 3   
1                       b5dae48681351a2f70efde3e7d2be6dd                 3   
0      (b1aeaf37d0bd4027abc939b89d39e693, 90e8cd12bbf...               156   
1      (b1aeaf37d0bd4027abc939b89d39e693, 9a6bb4142ca...               156   
2      (b1aeaf37d0bd4027abc939b89d39e693, d62e007d22e...               570   
...                                                  ...               ...   
14116  (10b4122ac22b41aba6a007c810296a90, c8234c88a5e...                 3   
14117  (10b4122ac22b41aba6a007c810296a90, be605eaacd9...                 3   
14118  (10b4122ac22b41aba6a007c810296a90, 0f97cf00e49...                 3   
14119  (10b4122ac22b41aba6a007c810296a90, bc96527e31b...                 3   
14120  (10b4122ac22b41aba6a007c810296a90, f63648bbd67...                 3   

         Installation  Technology        Placement        Build Placement2  \
0       slanted-roof    single-Si            panel      mounted    on roof   
1       slanted-roof     multi-Si            panel      mounted    on roof   
0          flat-roof     multi-Si          on roof         None       None   
1          flat-roof    single-Si          on roof         None       None   
2        open ground          CIS   on open ground         None       None   
...               ...         ...              ...          ...        ...   
14116   slanted-roof         CdTe        laminated   integrated    on roof   
14117   slanted-roof     multi-Si        laminated   integrated    on roof   
14118   slanted-roof     multi-Si            panel      mounted    on roof   
14119   slanted-roof    single-Si        laminated   integrated    on roof   
14120   slanted-roof    single-Si            panel      mounted    on roof   

       fake_efficiencies  previous production  new production  \
0                   1400         8.298067e+04          126000   
1                   1400         8.298067e+04          126000   
0                   1400         4.567680e+06         6552000   
1                   1400         4.567680e+06         6552000   
2                   1400         1.778400e+07        23940000   
...                  ...                  ...             ...   
14116               1400         1.055700e+05          126000   
14117               1400         1.055700e+05          126000   
14118               1400         1.055700e+05          126000   
14119               1400         1.055700e+05          126000   
14120               1400         1.055700e+05          126000   

       Exchange Variation  
0                0.658577  
1        

In [129]:
selected_cols = ['Market group location','Peak power (kWp)','Installation','Technology']

pv_datasets['combined_data'] = pv_datasets['Market group location'] + pv_datasets['Peak power (kWp)'].astype(str)+pv_datasets['Installation']+pv_datasets['Technology']
print(len(pv_datasets['combined_data'].unique()))

pv_datasets['combined_data2'] = pv_datasets['Market group location']+pv_datasets['Installation']+pv_datasets['Technology']
print(len(pv_datasets['combined_data2'].unique()))

pv_datasets['combined_data3'] = pv_datasets['Installation']+pv_datasets['Technology']
print(len(pv_datasets['combined_data3'].unique()))

print(26*14)

469
365
14
364


### Figure out the amount of square meters and expected lifespan of the panels

In [154]:
for ds in bd.Database(the_db) :
    if ('photovoltaic' in ds['name']) & (ds['unit']=='unit') & ('market' not in ds['name']): 
        #print(ds['name'])
        try : 
            year = int(ds['comment'].split(' years')[0][-2:])
            print(ds['name'],year)
        except : 
            print(f"--->{ds['name']} has no numerical year.")
    
   # pass

photovoltaic flat-roof installation, 3kWp, multi-Si, on roof 30
photovoltaic slanted-roof installation, 3kWp, multi-Si, panel, mounted, on roof 30
photovoltaic slanted-roof installation, 3kWp, single-Si, panel, mounted, on roof 30
photovoltaic flat-roof installation, 3kWp, single-Si, on roof 30
--->photovoltaics, electric installation for 3kWp module, at building has no numerical year.
photovoltaic slanted-roof installation, 3kWp, CdTe, laminated, integrated, on roof 30
photovoltaic slanted-roof installation, 3kWp, multi-Si, laminated, integrated, on roof 30
photovoltaic facade installation, 3kWp, single-Si, laminated, integrated, at building 30
photovoltaic slanted-roof installation, 3kWp, multi-Si, laminated, integrated, on roof 30
photovoltaic slanted-roof installation, 3kWp, a-Si, panel, mounted, on roof 30
photovoltaic slanted-roof installation, 3kWp, a-Si, laminated, integrated, on roof 30
photovoltaic slanted-roof installation, 3kWp, CIS, panel, mounted, on roof 30
photovoltaic 

In [201]:
for row in pv_datasets.iterrows() : 
    ds = bd.get_activity((the_other_db2,row[1]['Underlying PV tech code']))
    
    
    print(ds['name'],ds['location'],ds['reference product'])

electricity production, photovoltaic, 3kWp slanted-roof installation, single-Si, panel, mounted, renewable energy produc CH electricity, low voltage, renewable energy products
electricity production, photovoltaic, 3kWp slanted-roof installation, multi-Si, panel, mounted, renewable energy product CH electricity, low voltage, renewable energy products
photovoltaic flat-roof installation, 156 kWp, multi-Si, on roof CH photovoltaic flat-roof installation, 156 kWp, multi-Si, on roof
photovoltaic flat-roof installation, 156 kWp, single-Si, on roof CH photovoltaic flat-roof installation, 156 kWp, single-Si, on roof
photovoltaic open ground installation, 570 kWp, CIS, on open ground RER photovoltaic open ground installation, 570 kWp, CIS, on open ground
photovoltaic open ground installation, 570 kWp, CdTe, on open ground RER photovoltaic open ground installation, 570 kWp, CdTe, on open ground
photovoltaic open ground installation, 570 kWp, micro-Si, on open ground RER photovoltaic open ground 

In [200]:
for row in pv_datasets.iterrows() : 
    ds = bd.get_activity((the_other_db2,row[1]['Underlying PV tech code']))
    print('--->',ds['name'])
    for exc in ds.exchanges() : 
        if ('photovoltaic' in exc['name']) & (exc['unit']=='unit') & ('kWp' in exc['name']) :#& ('electric inst' not in exc['name']): 
           # print(exc['type'])
            #pv_unit_ds = bd.get_activity((the_other_db2,exc.input['code']))
            print(exc['amount'],exc['unit'],exc['type'],exc['name'])
            #if 'market' in exc['name'] :
            #    print('oops - market!')


            

            #print(exc.input.as_dict().keys())#['amount'])
            #for exc2 in pv_unit_ds.exchanges(): 
            #    #print(exc2['name'])
            #    if (exc2['unit'] =='square meter') & ('mounting' not in exc2['name']) & (exc2['type'] != 'production') & ('panel' in exc2['name']):
            #        print(exc2['name'],exc2.amount)
                                    


---> electricity production, photovoltaic, 3kWp slanted-roof installation, single-Si, panel, mounted, renewable energy produc
1.2051e-05 unit technosphere photovoltaic slanted-roof installation, 3kWp, single-Si, panel, mounted, on roof
---> electricity production, photovoltaic, 3kWp slanted-roof installation, multi-Si, panel, mounted, renewable energy product
1.2051e-05 unit technosphere photovoltaic slanted-roof installation, 3kWp, multi-Si, panel, mounted, on roof
---> photovoltaic flat-roof installation, 156 kWp, multi-Si, on roof
1.0 unit production photovoltaic flat-roof installation, 156 kWp, multi-Si, on roof
1.0 unit technosphere electric installation, 156 kWp photovoltaic plant, at plant
---> photovoltaic flat-roof installation, 156 kWp, single-Si, on roof
1.0 unit production photovoltaic flat-roof installation, 156 kWp, single-Si, on roof
1.0 unit technosphere electric installation, 156 kWp photovoltaic plant, at plant
---> photovoltaic open ground installation, 570 kWp, CIS,

In [210]:
DAC_ds = 'carbon dioxide, captured from atmosphere, with a solvent-based direct air capture system, 1MtCO2'


In [215]:
for ds in bd.Database(the_other_db2) : 
    if ds['name'] == DAC_ds : 
        print(ds['name'],'----',ds['unit'])
        for exc in ds.exchanges(): 
            print(exc['name'], exc['type'])

carbon dioxide, captured from atmosphere, with a solvent-based direct air capture system, 1MtCO2 ---- kilogram
carbon dioxide, captured from atmosphere, with a solvent-based direct air capture system, 1MtCO2 production
direct air capture system, solvent-based, 1MtCO2 technosphere
treatment of direct air capture system, solvent-based, 1MtCO2 technosphere
market for tap water technosphere
market for potassium hydroxide technosphere
market for limestone, crushed, for mill technosphere
Carbon dioxide, in air biosphere
Carbon dioxide, non-fossil biosphere
market group for electricity, medium voltage technosphere
heat production, natural gas, at industrial furnace >100kW technosphere


In [104]:
import pickle
with open(fr"pv_details{the_other_db}.pickle", "wb") as output_file:
    pickle.dump(pv_datasets, output_file)

In [214]:
# storage = []

# for ds in bd.Database('SSP2-RCP19-2050') : 
#     if 'market for electricity' in ds['name']: 

#         for exc1 in ds.exchanges() : 
# #            print(exc1)
#             if 'market group for electricity' in exc1['name']:
#                 #print(exc1['name'])
#                 for exc2 in bd.get_activity(exc1['input']).exchanges():
#                 #print(bd.get_activity(exc1['input']))
#                 #for exc2 in exc1.exchanges(): 
#                     if 'photovoltaic' in exc2['name']:
#                         #print(exc2['name'],bd.get_activity(exc2['input'])['name'])
                        
#                         for exc3 in bd.get_activity(exc2['input']).exchanges(): 
#                             #print(exc3['name'])
#                             if 'photovoltaic' in exc3['name'] : 
#                                 strings = str(exc3['name']).split(',')
#                                 #print(strings)

#                                 # Clear non production datasets
#                                 if not any('kWp' in s for s in strings) : 
#                                     #print('here')
#                                     continue

#                                 # Edit the strings :
#                                 if 'MWp' in strings[1] : 
#                                     strings[1] = 1000*int(strings[1].replace('MWp',''))
#                                 if 'kWp' in strings[1] : 
#                                     strings[1] = int(strings[1].replace('kWp',''))
#                                 if 'installation' in strings[0] : 
#                                     strings[0] = strings[0].replace('installation','')
#                                 if 'photovoltaic' in strings[0] : 
#                                     strings[0] = strings[0].replace('photovoltaic','')

#                                 storage.append((ds['name'],ds['location'],exc1['location'],*strings))

            
# import pandas as pd
# df = pd.DataFrame(storage)
# df.columns= ['Market Dataset','ecoinvent location','Market group location','Installation','Peak power','Technology','Placement','Build','Placement2']
# display(df)

# import pickle
# with open(r"pv_details.pickle", "wb") as output_file:
#     pickle.dump(df, output_file)

Market Dataset ecoinvent location  \
0      market for electricity, high voltage             US-MRO   
1      market for electricity, high voltage             US-MRO   
2      market for electricity, high voltage             US-MRO   
3      market for electricity, high voltage             US-MRO   
4      market for electricity, high voltage             US-MRO   
...                                     ...                ...   
14116  market for electricity, high voltage             CN-NWG   
14117  market for electricity, high voltage             CN-NWG   
14118  market for electricity, high voltage             CN-NWG   
14119  market for electricity, high voltage             CN-NWG   
14120  market for electricity, high voltage             CN-NWG   

      Market group location    Installation  Peak power  Technology  \
0                       USA      flat-roof          156    multi-Si   
1                       USA      flat-roof          156   single-Si   
2                       USA    open ground          570         CIS   
3                       USA    open ground          570        CdTe   
4                       USA    open ground          570    micro-Si   
...                     ...             ...         ...         ...   
14116                   CHN    open ground          570   single-Si   
14117                   CHN   slanted-roof           93    multi-Si   
14118                   CHN   slanted-roof           93    multi-Si   
14119                   CHN   slanted-roof           93   single-Si   
14120                   CHN   slanted-roof           93   single-Si   

             Placement        Build Placement2  
0              on roof         None       None  
1              on roof         None       None  
2       on open ground         None       None  
3       on open ground         None       None  
4       on open ground         None       None  
...                ...          ...        ...  
14116   on open ground         None       None  
14117        laminated   integrated    on roof  
14118            panel      mounted    on roof  
14119        laminated   integrated    on roof  
14120            panel      mounted    on roof  

[14121 rows x 9 columns]